In [119]:
import pandas as pd
import numpy as np

#from sklearn.linear_model import LogisticRegression
from sklearn.linear_model import Ridge, Lasso, ElasticNet

from sklearn.metrics import r2_score
from sklearn.metrics import accuracy_score, roc_auc_score

from sklearn.model_selection import train_test_split
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import KFold
from sklearn.preprocessing import StandardScaler

#from sklearn.model_selection import StratifiedKFold

#from sklearn.naive_bayes import GaussianNB

from sklearn.pipeline import Pipeline
#from sklearn.discriminant_analysis import LinearDiscriminantAnalysis
#from sklearn.svm import SVC

from sklearn.tree import DecisionTreeRegressor, plot_tree
from sklearn.ensemble import VotingRegressor

In [120]:
con = pd.read_csv("Cases\Concrete Strength\Concrete_Data.csv")

In [121]:
con.head()

Cement  Blast  Fly  Water  Superplasticizer  Coarse   Fine  Age  Strength
0   540.0    0.0  0.0  162.0               2.5  1040.0  676.0   28     79.99
1   540.0    0.0  0.0  162.0               2.5  1055.0  676.0   28     61.89
2   332.5  142.5  0.0  228.0               0.0   932.0  594.0  270     40.27
3   332.5  142.5  0.0  228.0               0.0   932.0  594.0  365     41.05
4   198.6  132.4  0.0  192.0               0.0   978.4  825.5  360     44.30

In [122]:
y = con["Strength"]
X = con.drop("Strength", axis = 1)

In [123]:
X_train, X_test, y_train, y_test = train_test_split(X,
                                                    y,
                                                    random_state = 2022,
                                                    train_size = 0.7)

In [124]:
ridge = Ridge()

In [125]:
lasso = Lasso()

In [126]:
elastic= ElasticNet()

In [127]:
dtr = DecisionTreeRegressor(random_state = 2022)

# Without weights

In [128]:
voting = VotingRegressor([("Ridge", ridge), ("Lasso", lasso),
                          ("Elastic", elastic), ("Tree", dtr)])

voting.fit(X_train, y_train)

VotingRegressor(estimators=[('Ridge', Ridge()), ('Lasso', Lasso()),
                            ('Elastic', ElasticNet()),
                            ('Tree', DecisionTreeRegressor(random_state=2022))])

In [129]:
y_pred = voting.predict(X_test)
print(r2_score(y_test, y_pred))

0.7636552054757627


## Evaluating Regressors Separately

In [130]:
ridge = Ridge()
ridge.fit(X_train, y_train)

y_pred = ridge.predict(X_test)

r2_ridge = r2_score(y_test, y_pred)

print(r2_ridge)

0.6471645930971449


In [131]:
lasso = Lasso()
lasso.fit(X_train, y_train)

y_pred = lasso.predict(X_test)

r2_lasso = r2_score(y_test, y_pred)

print(r2_lasso)

0.645970160164322


In [133]:
elastic = ElasticNet()
elastic.fit(X_train, y_train)

y_pred = elastic.predict(X_test)

r2_elastic = r2_score(y_test, y_pred)

print(r2_elastic)

0.6465499867835319


In [134]:
dtr = DecisionTreeRegressor(random_state = 2022)
dtr.fit(X_train, y_train)

y_pred = elastic.predict(X_test)

r2_dtr = r2_score(y_test, y_pred)

print(r2_dtr)

0.6465499867835319


# With weights

In [135]:
voting = VotingRegressor([("Ridge", ridge), ("Lasso", lasso),
                          ("Elastic", elastic), ("Tree", dtr)],
                        weights = [r2_ridge, r2_lasso, r2_dtr, r2_elastic_net])

voting.fit(X_train, y_train)

VotingRegressor(estimators=[('Ridge', Ridge()), ('Lasso', Lasso()),
                            ('Elastic', ElasticNet()),
                            ('Tree', DecisionTreeRegressor(random_state=2022))],
                weights=[0.6471645930971449, 0.645970160164322,
                         0.6465499867835319, 0.6465499867835319])

In [136]:
y_pred = voting.predict(X_test)
print(y_pred)

[19.93297836 47.80263037 31.05936301 36.45280158 27.19779778 37.03999963
 42.11082805 36.17391818 32.72339729 44.85729084 47.48873328 22.89266948
 24.50164972 19.6293686  25.21368112 51.09458371 58.24783814 39.1361979
 26.50842017 46.26836822 69.65085527 41.52535595 52.01154251 35.46994246
 33.92323154 31.19954521 32.13776402 60.24948347 27.5695771  55.88298699
 56.49382985 30.55162887 25.4213056  54.6578515  39.33842987 56.56556113
 13.49226511 63.9480248  56.25422917 38.42060312 29.40610253 25.8343532
 31.35970866 52.11534828 49.67843804 61.09615977 19.14621507 25.33558577
 11.02501654 23.83454029 41.99972904 53.52978003 40.54157352 33.5212556
 25.56556532 61.67568983 23.72822569 22.97763203 48.66717431 22.74471043
 22.70847092 71.61589233 54.33610142 20.55191021 32.91792517 31.09456266
 29.73181345 39.40940058 37.70408549 24.47918573 21.42869236 44.20307123
 57.59575502 30.64857664 37.89765982 19.67694853 32.94899191 44.74369554
 59.72596851 31.0191134  50.62363291 20.50282301 24.71

In [137]:
print(r2_score(y_test, y_pred))

0.7636541512087678


# Grid Search CV

In [138]:
kfold = KFold(n_splits = 5,
                        shuffle = True,
                        random_state = 2022)

In [139]:
ridge = Ridge()
lasso = Lasso()
elastic = ElasticNet()
dtr = DecisionTreeRegressor(random_state = 2022)

voting = VotingRegressor([("Ridge", ridge), ("Lasso", lasso),
                          ("Elastic", elastic), ("Tree", dtr)])

In [140]:
voting = VotingRegressor([("RIDGE", ridge), ("LASSO", lasso),
                          ("ELASTIC", elastic), ("TREE", dtr)])

In [141]:
print(voting.get_params())

{'estimators': [('RIDGE', Ridge()), ('LASSO', Lasso()), ('ELASTIC', ElasticNet()), ('TREE', DecisionTreeRegressor(random_state=2022))], 'n_jobs': None, 'verbose': False, 'weights': None, 'RIDGE': Ridge(), 'LASSO': Lasso(), 'ELASTIC': ElasticNet(), 'TREE': DecisionTreeRegressor(random_state=2022), 'RIDGE__alpha': 1.0, 'RIDGE__copy_X': True, 'RIDGE__fit_intercept': True, 'RIDGE__max_iter': None, 'RIDGE__normalize': 'deprecated', 'RIDGE__positive': False, 'RIDGE__random_state': None, 'RIDGE__solver': 'auto', 'RIDGE__tol': 0.001, 'LASSO__alpha': 1.0, 'LASSO__copy_X': True, 'LASSO__fit_intercept': True, 'LASSO__max_iter': 1000, 'LASSO__normalize': 'deprecated', 'LASSO__positive': False, 'LASSO__precompute': False, 'LASSO__random_state': None, 'LASSO__selection': 'cyclic', 'LASSO__tol': 0.0001, 'LASSO__warm_start': False, 'ELASTIC__alpha': 1.0, 'ELASTIC__copy_X': True, 'ELASTIC__fit_intercept': True, 'ELASTIC__l1_ratio': 0.5, 'ELASTIC__max_iter': 1000, 'ELASTIC__normalize': 'deprecated', 'EL

In [142]:
params = {"RIDGE__alpha": np.linspace(0.001, 5, 5),
          "LASSO__alpha": np.linspace(0.001, 5, 5),
          "ELASTIC__alpha": np.linspace(0.001, 5, 5),
          "ELASTIC__l1_ratio": np.linspace(0, 1, 5),
          "TREE__max_depth": [None, 3],
          "TREE__min_samples_split": [2, 5, 10],
          "TREE__min_samples_leaf":[1,5,10]
    
}

In [143]:
gcv = GridSearchCV(voting,
                  param_grid = params,
                  cv = kfold, verbose = 3,
                  scoring = "neg_log_loss")

gcv.fit(X, y)

Fitting 5 folds for each of 11250 candidates, totalling 56250 fits


C:\Users\admin\anaconda3\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:647: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 4.641e+04, tolerance: 2.310e+01 Linear regression models with null weight for the l1 regularization term are more efficiently fitted using one of the solvers implemented in sklearn.linear_model.Ridge/RidgeCV instead.
  model = cd_fast.enet_coordinate_descent(
C:\Users\admin\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:770: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\admin\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 761, in _score
    scorer = _MultimetricScorer(**scorer)
  File "C:\Users\admin\anaconda3\lib\site-packages\sklearn\metrics\_

[CV 1/5] END ELASTIC__alpha=0.001, ELASTIC__l1_ratio=0.0, LASSO__alpha=0.001, RIDGE__alpha=0.001, TREE__max_depth=None, TREE__min_samples_leaf=1, TREE__min_samples_split=2;, score=nan total time=   0.4s
[CV 2/5] END ELASTIC__alpha=0.001, ELASTIC__l1_ratio=0.0, LASSO__alpha=0.001, RIDGE__alpha=0.001, TREE__max_depth=None, TREE__min_samples_leaf=1, TREE__min_samples_split=2;, score=nan total time=   0.0s
[CV 3/5] END ELASTIC__alpha=0.001, ELASTIC__l1_ratio=0.0, LASSO__alpha=0.001, RIDGE__alpha=0.001, TREE__max_depth=None, TREE__min_samples_leaf=1, TREE__min_samples_split=2;, score=nan total time=   0.0s
[CV 4/5] END ELASTIC__alpha=0.001, ELASTIC__l1_ratio=0.0, LASSO__alpha=0.001, RIDGE__alpha=0.001, TREE__max_depth=None, TREE__min_samples_leaf=1, TREE__min_samples_split=2;, score=nan total time=   0.0s


C:\Users\admin\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:770: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\admin\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 761, in _score
    scorer = _MultimetricScorer(**scorer)
  File "C:\Users\admin\anaconda3\lib\site-packages\sklearn\metrics\_scorer.py", line 216, in __call__
    -------
  File "C:\Users\admin\anaconda3\lib\site-packages\sklearn\metrics\_scorer.py", line 298, in _score
    Score function applied to prediction of estimator on X.
  File "C:\Users\admin\anaconda3\lib\site-packages\sklearn\metrics\_scorer.py", line 68, in _cached_call
AttributeError: 'VotingRegressor' object has no attribute 'predict_proba'

  raise
C:\Users\admin\anaconda3\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:647: ConvergenceWarning: Objective did not converge. You

[CV 5/5] END ELASTIC__alpha=0.001, ELASTIC__l1_ratio=0.0, LASSO__alpha=0.001, RIDGE__alpha=0.001, TREE__max_depth=None, TREE__min_samples_leaf=1, TREE__min_samples_split=2;, score=nan total time=   0.0s
[CV 1/5] END ELASTIC__alpha=0.001, ELASTIC__l1_ratio=0.0, LASSO__alpha=0.001, RIDGE__alpha=0.001, TREE__max_depth=None, TREE__min_samples_leaf=1, TREE__min_samples_split=5;, score=nan total time=   0.0s
[CV 2/5] END ELASTIC__alpha=0.001, ELASTIC__l1_ratio=0.0, LASSO__alpha=0.001, RIDGE__alpha=0.001, TREE__max_depth=None, TREE__min_samples_leaf=1, TREE__min_samples_split=5;, score=nan total time=   0.0s
[CV 3/5] END ELASTIC__alpha=0.001, ELASTIC__l1_ratio=0.0, LASSO__alpha=0.001, RIDGE__alpha=0.001, TREE__max_depth=None, TREE__min_samples_leaf=1, TREE__min_samples_split=5;, score=nan total time=   0.0s
[CV 4/5] END ELASTIC__alpha=0.001, ELASTIC__l1_ratio=0.0, LASSO__alpha=0.001, RIDGE__alpha=0.001, TREE__max_depth=None, TREE__min_samples_leaf=1, TREE__min_samples_split=5;, score=nan tota

...

C:\Users\admin\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:770: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\admin\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 761, in _score
    scorer = _MultimetricScorer(**scorer)
  File "C:\Users\admin\anaconda3\lib\site-packages\sklearn\metrics\_scorer.py", line 216, in __call__
    -------
  File "C:\Users\admin\anaconda3\lib\site-packages\sklearn\metrics\_scorer.py", line 298, in _score
    Score function applied to prediction of estimator on X.
  File "C:\Users\admin\anaconda3\lib\site-packages\sklearn\metrics\_scorer.py", line 68, in _cached_call
AttributeError: 'VotingRegressor' object has no attribute 'predict_proba'

  raise
C:\Users\admin\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:770: UserWarning: Scoring failed. The score on this train-tes

[CV 5/5] END ELASTIC__alpha=0.001, ELASTIC__l1_ratio=0.25, LASSO__alpha=1.2507499999999998, RIDGE__alpha=5.0, TREE__max_depth=None, TREE__min_samples_leaf=1, TREE__min_samples_split=2;, score=nan total time=   0.0s
[CV 1/5] END ELASTIC__alpha=0.001, ELASTIC__l1_ratio=0.25, LASSO__alpha=1.2507499999999998, RIDGE__alpha=5.0, TREE__max_depth=None, TREE__min_samples_leaf=1, TREE__min_samples_split=5;, score=nan total time=   0.0s
[CV 2/5] END ELASTIC__alpha=0.001, ELASTIC__l1_ratio=0.25, LASSO__alpha=1.2507499999999998, RIDGE__alpha=5.0, TREE__max_depth=None, TREE__min_samples_leaf=1, TREE__min_samples_split=5;, score=nan total time=   0.0s
[CV 3/5] END ELASTIC__alpha=0.001, ELASTIC__l1_ratio=0.25, LASSO__alpha=1.2507499999999998, RIDGE__alpha=5.0, TREE__max_depth=None, TREE__min_samples_leaf=1, TREE__min_samples_split=5;, score=nan total time=   0.0s
[CV 4/5] END ELASTIC__alpha=0.001, ELASTIC__l1_ratio=0.25, LASSO__alpha=1.2507499999999998, RIDGE__alpha=5.0, TREE__max_depth=None, TREE__mi

C:\Users\admin\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:770: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\admin\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 761, in _score
    scorer = _MultimetricScorer(**scorer)
  File "C:\Users\admin\anaconda3\lib\site-packages\sklearn\metrics\_scorer.py", line 216, in __call__
    -------
  File "C:\Users\admin\anaconda3\lib\site-packages\sklearn\metrics\_scorer.py", line 298, in _score
    Score function applied to prediction of estimator on X.
  File "C:\Users\admin\anaconda3\lib\site-packages\sklearn\metrics\_scorer.py", line 68, in _cached_call
AttributeError: 'VotingRegressor' object has no attribute 'predict_proba'

  raise
C:\Users\admin\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:770: UserWarning: Scoring failed. The score on this train-tes

[CV 2/5] END ELASTIC__alpha=0.001, ELASTIC__l1_ratio=0.25, LASSO__alpha=1.2507499999999998, RIDGE__alpha=5.0, TREE__max_depth=None, TREE__min_samples_leaf=5, TREE__min_samples_split=2;, score=nan total time=   0.0s
[CV 3/5] END ELASTIC__alpha=0.001, ELASTIC__l1_ratio=0.25, LASSO__alpha=1.2507499999999998, RIDGE__alpha=5.0, TREE__max_depth=None, TREE__min_samples_leaf=5, TREE__min_samples_split=2;, score=nan total time=   0.0s
[CV 4/5] END ELASTIC__alpha=0.001, ELASTIC__l1_ratio=0.25, LASSO__alpha=1.2507499999999998, RIDGE__alpha=5.0, TREE__max_depth=None, TREE__min_samples_leaf=5, TREE__min_samples_split=2;, score=nan total time=   0.0s
[CV 5/5] END ELASTIC__alpha=0.001, ELASTIC__l1_ratio=0.25, LASSO__alpha=1.2507499999999998, RIDGE__alpha=5.0, TREE__max_depth=None, TREE__min_samples_leaf=5, TREE__min_samples_split=2;, score=nan total time=   0.0s
[CV 1/5] END ELASTIC__alpha=0.001, ELASTIC__l1_ratio=0.25, LASSO__alpha=1.2507499999999998, RIDGE__alpha=5.0, TREE__max_depth=None, TREE__mi

KeyboardInterrupt: 

In [99]:
print(voting.get_params().keys())

dict_keys(['estimators', 'n_jobs', 'verbose', 'weights', 'RIDGE', 'LASSO', 'ELASTIC', 'TREE', 'RIDGE__alpha', 'RIDGE__copy_X', 'RIDGE__fit_intercept', 'RIDGE__max_iter', 'RIDGE__normalize', 'RIDGE__positive', 'RIDGE__random_state', 'RIDGE__solver', 'RIDGE__tol', 'LASSO__alpha', 'LASSO__copy_X', 'LASSO__fit_intercept', 'LASSO__max_iter', 'LASSO__normalize', 'LASSO__positive', 'LASSO__precompute', 'LASSO__random_state', 'LASSO__selection', 'LASSO__tol', 'LASSO__warm_start', 'ELASTIC__alpha', 'ELASTIC__copy_X', 'ELASTIC__fit_intercept', 'ELASTIC__l1_ratio', 'ELASTIC__max_iter', 'ELASTIC__normalize', 'ELASTIC__positive', 'ELASTIC__precompute', 'ELASTIC__random_state', 'ELASTIC__selection', 'ELASTIC__tol', 'ELASTIC__warm_start', 'TREE__ccp_alpha', 'TREE__criterion', 'TREE__max_depth', 'TREE__max_features', 'TREE__max_leaf_nodes', 'TREE__min_impurity_decrease', 'TREE__min_samples_leaf', 'TREE__min_samples_split', 'TREE__min_weight_fraction_leaf', 'TREE__random_state', 'TREE__splitter'])


In [ ]:
print(gcv.best_score_)

In [106]:
print(gcv.best_score_)

nan
